# Exame 2022/2023

In [ ]:
import pip

def import_or_install(package):
    try:
        __import__(package)
    except ImportError:
        pip.main(['install', package])

import_or_install('numpy_financial')

Please see https://github.com/pypa/pip/issues/5599 for advice on fixing the underlying issue.
To avoid this problem you can invoke Python with '-m pip' instead of running pip directly.


Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/

Collecting numpy_financial

Downloading numpy_financial-1.0.0-py3-none-any.whl (14 kB)

Requirement already satisfied: numpy>=1.15 in /usr/local/lib/python3.8/dist-packages (from numpy_financial) (1.21.6)

Installing collected packages: numpy_financial

Successfully installed numpy_financial-1.0.0

In [ ]:
import numpy_financial as npf
import pandas as pd
import scipy
import math

from scipy.stats import binom
from numpy import log as ln
from numpy import log as ln


def create_frequency_table(df, bins, column):
    df = pd.DataFrame(df[column]).groupby(pd.cut(df[column], bins)).count()
    df.columns = ['Frequência Absoluta']
    df['Frequência relativa (%)'] = round(df['Frequência Absoluta'] /
                                    df['Frequência Absoluta'].sum() * 100, 2)
    df['Frequência Absoluta acumulada'] = df['Frequência Absoluta'].cumsum()
    df['Frequência relativa acumulada (%)'] = df['Frequência relativa (%)'].cumsum()
    return df

def compute_continuous_return(pv, fv):
    return ln(fv/pv)

def compute_srf(mean, std, minimum_value):
    return (mean - minimum_value) / (std)

def compute_normal_cdf(mu, std, value):
    return scipy.stats.norm(mu, std).cdf(value)

def compute_uniform_cdf_continuous(min_value, max_value, value):
    if value < max_value and value > min_value:
        return (value - min_value)  / (max_value - min_value)
    else:
        return ("Error: value is probably not betwwen the min and max values")

def compute_binomial_pmf(p, n, k):
    '''
    p = probabilidade de sucesso
    n = número de tentativas
    k = número de sucessos
    '''
    return scipy.stats.binom.pmf(p=p, n=n, k=k)

def compute_binomial_cdf(p, n, k):
    '''
    p = probabilidade de sucesso
    n = número de tentativas
    k = número de sucessos
    '''
    return scipy.stats.binom.cdf(p=p, n=n, k=k)

def compute_binomial_var(p, n):
    '''
    p = probabilidade de sucesso
    n = número de tentativas
    '''
    return scipy.stats.binom.var(p=p, n=n)

def compute_binomial_std(p, n):
    '''
    p = probabilidade de sucesso
    n = número de tentativas
    '''
    return scipy.stats.binom.std(p=p, n=n)

def compute_FV_ordinary_annuity(A, r, N):

    # A = Pagamento / cash flow
    # r = taxa de juro
    # N = Nr. de anos

    FV = A * (((1+r)**N -1) / r)
    return FV

def compute_FV_lump_sum(PV, rs, N, m=1):

    # FV = Future value / valor futuro
    # PV = Present value / Valor actual
    # rs = Stated rate / Taxa de juro cotada
    # N = número de anos

    FV = PV * (1+rs/m)**(N*m)
    return FV

def compute_PV_lump_sum(FV, rs, N, m=1):

    # PV = Present Value
    # rs = taxa de juro
    # N = Nr de anos/períodos
    # m = 1 para ter capitalizaçãoo anual por defeito

    PV = FV * (1+(rs/m))**(-N*m)
    return PV

def compute_PV_ordinary_annuity(A, r, N):

    # A = Pagamento / cash flow
    # r = taxa de juro
    # N = Nr. de anos

    PV = A * (1-1/(1+r)**N)/ r
    return PV

def compute_PV_ordinary_annuity_ucf(cf, r, m=1):
    PV_total = 0
    N=0
    for cash_flow in cf:
        N = N + 1
        PV = compute_PV_lump_sum(cash_flow, rs=r, N=N)
        PV_total = PV_total + PV

    return PV_total

def compute_pmt(FV, rs, N):

    # FV = Future value / valor futuro
    # rs = taxa de juro
    # N = Nr de anos/per�odos
    # pmt = pagamento

    pmt = npf.pmt(rate=rs, nper=N, fv=FV, pv=0)
    return pmt

def compute_PV_annuity_due(A, r, N):
    PV = (A * ((1-(1+r)**-N)) / r) * (1+r)
    return PV

def compute_ear(rs, m):

    # FV = Future value / valor futuro
    # PV = Present value / Valor actual
    # rs = Stated rate / Taxa de juro cotada
    # m = n�mero de capitaliza��es anuais

    ear = (1 + rs/m)**m -1
    return ear

def compute_N(FV, PV, r):
    N = ln(FV/PV) / ln(1+r)
    return N

def compute_FV_lump_sum_continuous(PV, rs, N):

    # FV = Future value / valor futuro
    # PV = Present value / Valor actual
    # rs = Stated rate / Taxa de juro cotada
    # N = n�mero de anos

    FV = PV * math.e**(rs*N)
    return FV

def compute_PV_perpetuity(A, r, m=1):
    return A/(r/m)

def compute_FV_ordinary_annuity_ucf(cf, r, N, m=1):

    # ucf = unequal cash flows
    # cf = série de cash flows
    # r = taxa de juro
    # N = Nr de anos

    FV_total = 0 # criar uma variável para somar os valores futuros dos cash flows

    for cash_flow in cf: # Para cada cash flow na série de cash flows
        N = N - 1
        FV = compute_FV_lump_sum(cash_flow, rs=r, N=N) # calcular o cash flow
        FV_total = FV_total + FV # somar cada valor futuro ao valor total

    return FV_total

def compute_g(FV, PV, N):
    g = ((FV/PV)**(1/N))-1
    return g

def compute_A(PV, rs, N, m=1):
    PVAF = (1-1/(1+(rs/m))**(m*N))/(rs/m)
    A=PV/PVAF
    return A

def normalize(df):
    df = df.dropna()
    return (df / df.iloc[0]) * 100

def compute_binomial_pmf(p, n, k):
    '''
    p = probabilidade de sucesso
    n = número de tentativas
    k = número de sucessos
    '''
    return scipy.stats.binom.pmf(p=p, n=n, k=k)

def compute_binomial_cdf(p, n, k):
    '''
    p = probabilidade de sucesso
    n = número de tentativas
    k = número de sucessos
    '''
    return scipy.stats.binom.cdf(p=p, n=n, k=k)

def compute_binomial_var(p, n):
    '''
    p = probabilidade de sucesso
    n = número de tentativas
    '''
    return scipy.stats.binom.var(p=p, n=n)

def compute_binomial_std(p, n):
    '''
    p = probabilidade de sucesso
    n = número de tentativas
    '''
    return scipy.stats.binom.std(p=p, n=n)

NumExpr defaulting to 2 threads.

## Capítulo 1

### Questão 1

Um investidor está a contemplar um investimento em obrigações 5 anos. Comparou obrigações a 5 anos do Tesouro Português e uma obrigação a 5 anos da Mota Engil. Enquanto a obrigação do Tesouro tinha uma yield de 3.5% a da Mota Engil apresentava uma yield de 5%. Esta diferença deve-se a:

a) Prémio de Insolvência  
b) Prémio de Maturidade  
c) Prémio de Inflação  

### Questão 2

Um aforrador pretende fazer um depósito a prazo e está a considerar os seguintes bancos:

- Banco A oferece uma taxa de 5.85% com capitalização anual;
- Banco B oferece uma taxa de 5.75% com capitalização mensal
- Banco C oferece uma taxa de 5.7% com capitalização diária

Assumindo que o aforrador vai o depósito que paga mais no final do ano qual o banco que ele escolhe:

a) O banco A  
b) O banco B  
c) O banco C

### Questão 3

Um investidor fez um investimento de 500 euros num ETF há 4 anos atrás. Obteve uma rentabilidade anualizada de 7.5%. Assumindo que o ETF é acumulativo (não pagou juros nem fez qualquer tipo de distribuição de rendimento) qual é o valor que o investidor tem ao dia de hoje?

A) 892€  
B) 650€  
C) 668€





### Questão 4

Um investidor pretende poupar 2000 euros ao ano durante os próximos 45 anos numa conta reforma que tem uma taxa de 8.5%. O valor aproximado que o investidor terá no final dos 45 anos será de:

A) 900 000 euros  
B) 270 000 euros  
C) 180 000 euros


### Questão 5

Uma acção preferencial paga um dividendo de 3.75 euros por acção. Assumindo que um investidor pretende ganhar um retorno de 8.5% qual o valor máximo que ele está disposto a pagar pela acção?

A) 31,88 €  
B) 44,12 €  
C) 42,10 €

## Capítulo 2

### Questão 6

Qual o melhor tipo de gr￡fico para visualizarmos uma s￩rie temporal? (cole￧￣o de observa￧￵es de dados num￩ricos feitas sequencialmente ao longo do tempo )

A) Mapa de calor;  
B) Nuvem de palavras;  
C) Gráfico de linhas.

### Questão 7

Qual das seguintes frases é **falsa**, assumindo que estamos a ver rentabilidade de um investimento:

A) A média geométrica é sempre superior ou igual à média aritmética;  
B) A média geométrica é sempre inferior ou igual à média aritmética;  
C) O diferencial entre a média geométrica e a média aritmética na rentabilidade de um investimento é tanto maior quanto maior for o desvio padrão dos retornos desse investimento.



### Questão 8

Vamos assumir que a morningstar divide equitativamente os fundos em categorias entre 1 e 5 estrelas com base na sua performance, face aos rivais, nos últimos 3 anos (ou seja por quintis), sendo que os melhores têm 5 estrelas e os piores 1 estrela. Quantas estrelas tem um fundo que bateu 75% dos rivais nos últimos 3 anos?

A) 3 estrelas  
B) 4 estrelas   
C) 5 estrelas

### Questão 9

Um investidor tem um portfolio que consiste em 7000 €uros no ETF A e 5000 €uros no ETF B. No ano de 2021 o ETF A teve uma performance de 20% e o ETF B teve uma performance de 10%. Qual foi a performance da carteira do investidor?

A) 15,8%  
B) 15%  
C) 30%

### Questão 10

Na teoria da probabilidade, eventos mutuamente exclusivos são melhor descritos como o conjunto de eventos que:

A) Não podem acontecer ao mesmo tempo;  
B) Incluem todos os resultados potenciais;   
C) Podem acontecer simultâneamente.

### Questão 11

Qual parâmetro é igual a 3 numa distribuição normal padrão?

A) Curtose  
B) Assimetria  
C) Desvio padrão

### Questão 12

A acção X tem um desvio padrão dos retornos de 18.9% e a acção Y tem um desvio padrão de 14.73%. Assumindo que as acções são perfeita e positivamente correlacionadas qual o desvio padrão de um portfolio com pesos iguais em ambas as acções?

A) 10.25%  
B) 14.67%  
C) 16.82%

### Questão 13

A resposta à questão 12 seria diferente se as acções não fossem perfeita e positivamente correlacionadas porque, caso não o fossem, **aumentava**:

A) A diversificação;  
B) A rentabilidade;  
C) O desvio padrão.

### Questão 14

Uma empresa muito grande tem quantidades iguais de funcionários homens e mulheres. Se uma amostra aleatória de quatro funcionários for selecionada, qual é a probabilidade de que todos os quatro funcionários selecionados sejam mulheres?

A) 0.0256  
B) 0.1600  
C) 0.0625

## Capítulo 4

### Questão 15

Para uma distribuição uniforme contínua que só pode assumir valores entre 2 e 10, a
probabilidade de um resultado:

A) igual a 4 é de 11,1%;  
B) menor que 3 é de 12,5%;  
C) maior que 5 é de 27,5%.

### Questão 16

A probabilidade de uma variável aleatória normalmente distribuída ter um valor  mais de dois desvios padrão **acima** da sua média é:

A) 0,0456;  
B) 0,0228;  
C) 0,9772

### Questão 17:

Um investimento tem um retorno esperado de 10% com um desvio padrão de 5%. Se os retornos são normalmente distribuídos, a probabilidade de perda de dinheiro é a mais próxima de:

A) 10,0%;  
B) 5,0%;  
C) 2,3%.

### Questão 18

Uma variável aleatória que tem um número contável de valores possíveis é melhor descrita como:

A) Uma variável aleatória discreta;  
B) Distribuição de probabilidade;  
C) Uma variável aleatória contínua.  

### Questão 19

Qual das seguintes afirmações sobre a distribuição t é a mais precisa/verdadeira?

A) A distribuição t tem assimetria positiva;  
B) A distribuição t tem caudas mais finas em comparação com a distribuição normal;  
C) A distribuição t aproxima-se da distribuição normal padrão à medida que os graus de liberdade aumentam.  

## Capítulo 5

### Questão 20

Thomas Merton, um analista da indústria automóvel, pretende investigar uma relação entre os tipos de anúncios utilizados em campanhas publicitárias e as vendas a clientes em determinados grupos de idade. Para garantir que inclua fabricantes de todos os tamanhos, Merton divide a indústria em quatro grupos de tamanho e retira amostras aleatórias de cada grupo. Qual método de amostragem Merton está a usar?

A) Amostragem transversal  
B) Amostragem aleatória estratificada  
C) Amostragem simples aleatória

### Questão 21

Ao aumentar tamanho da amostra aumenta, qual das seguintes afirmações **melhor** descreve a mudança no erro padrão da média amostral e o tamanho do intervalo de confiança para a verdadeira média?

A) O erro padrão diminui e o intervalo de confiança estreita  
B) O intervalo de confiança amplia enquanto o erro padrão diminui  
C) O erro padrão aumenta enquanto o intervalo de confiança estreita

### Questão 22

Um cientista que trabalha para uma empresa farmcêutica tenta vários modelos usando os mesmaos dados antes de relatar aquele que mostra que o medicamento dado não tem efeitos colaterias graves.

Os resultados do cientista são mais propensos a exibir:

A) Enviesamento de antecipação (Look-ahead bias)  
B) Enviesamento de sobrevivência (Survivourship bias)  
C) Enviesamento de manipulação de dados (Data-Snooping Bias)  

### Questão 23

Numa análise ao retorno anual médio ao longo de 20 anos para um setor de fundos de investimento o analista usou apenas uma amostra de fundos desse setor que possuem histórico de desempenho de 20 anos. A média de rentabilidades:

A) expressa de forma justa os retornos do setor de fundos  
B) subestima os retornos do setor de fundos  
C) Sobrestima os retornos do setor de fundos

### Questão 24:

Um analista está a testar a hipótese que o retorno excessivo médio de uma estratégia de negociação é menor ou igual a zero. O analista relata que este teste de hipótese produz um valor-p de 0,034. Isso sugere provavelmente que:

A) A melhor estimativa do retorno excessivo médio produzido pela estratégia é de 3,4%  
B) A hipótese nula pode ser rejeitada no nível de significância de 5%  
C) O menor nível de significância no qual a hipótese nula pode ser rejeitada é de 6,8%  

### Questão 25:

Joe Sutton está a avaliar os efeitos da queda de mercado de 1987 no volume de negociação. Especificamente, ele quer testar se a queda afetou o volume de negociação. Ele selecionou uma amostra de 500 empresas e recolheu dados sobre o volume total nos 12 meses antes da queda e nos 12 meses a seguir à queda. Qual é o conjunto de hipóteses que Sutton está a testar?

A) Ho: μd = μd0 versus Ha: μd > μd0  
B) Ho: μd = μd0 versus Ha: μd ≠ μd0  
C) Ho: μd ≠ μd0 versus Ha: μd = μd0

### Questão 26:

Se a probabilidade de um erro do tipo I diminui, então a probabilidade de:

A) um erro do tipo II aumenta  
B) aceitar incorretamente a hipótese nula diminui  
C) rejeitar incorretamente a hipótese nula aumenta  



### Questão 27:

O coeficiente de determinação (R^2) para uma regressão linear é melhor descrito como:

A) percentagem da variação da variável dependente explicada pela variação da variável independente  
B) covariância das variáveis ​​independentes e dependentes  
C) percentagem da variação da variável independente explicada pela variação da variável dependente

### Questão 28:

Qual dos seguintes é **menos provável** ser um pressuposto da regressão linear?

A) Os valores da variável independente não estão correlacionados com o termo de erro  
B) Os termos de erro de uma regressão são positivamente correlacionados   
C) A variância dos termos de erro de cada período permanece a mesma

### Questões 29 e 30 dizem respeito ao seguinte texto:

Damon Washburn, CFA, está atualmente matriculado como estudante de pós-graduação. Uma de suas recentes atribuições para seu curso de Análise Quantitativa é realizar uma análise de regressão utilizando os conceitos abordados durante o semestre. Ele deve interpretar os resultados da regressão, bem como as estatísticas de teste. Washburn está confiante na sua capacidade de calcular as estatísticas porque a turma pode usar software estatístico.
No entanto, ele percebe que a interpretação das estatísticas será o verdadeiro teste de sua conhecimento de análise de regressão. O seu professor deu aos alunos uma lista de perguntas que deve ser respondida pelos resultados da análise.

Washburn estimou uma equação de regressão na qual 160 retornos trimestrais do S&P 500 são explicados por três variáveis ​​macroeconômicas:

Crescimento do emprego (EMP) como medida por folha de pagamento não-agrícola;  
Crescimento do produto interno bruto (PIB);  
Investimento (INV).

Os resultados da análise de regressão são os seguintes:

![](https://s3.us-east-2.amazonaws.com/cbs.pg.repository/teste_29.png)

### Questão 29:

Qual é o retorno trimestral previsto para as acções, dadas as seguintes previsões?  

Crescimento do emprego = 2,0%  
Crescimento do PIB = 1,0%  
Crescimento do investimento privado = -1,0%  

A) 4,7%  
B) 5,0%  
C) 4,4%

### Questão 30

De acordo com a estatística Durbin-Watson, existe:

A) heterocedasticidade significativa nos resíduos  
B) nenhuma correlação em série positiva significativa nos resíduos  
C) correlação em série positiva significativa nos resíduos

### Questão 31

Uma série temporal possui quantos componentes?

A) 1  
B) 2  
C) 3  
D) 4

### Questão 32

A figura apresenta os primeiros 26 termos de uma série temporal. Sabendo que a equação da regressão estimada para a série temporal é  $Y_t=16,23 + 0,52Y_{t−1}+0,37Y_{t−2}$ determine o valor previsto para o período de tempo 27? (devem clicar na imagem para a ver com maiores dimensões)

![](https://s3.us-east-2.amazonaws.com/cbs.pg.repository/teste_32.png)

a) 53,32  
b) 109,5  
c) 116,65  
d) 116,95  

### Questão 33

A linha de tendência mais adequada para uma série temporal é aquela para a qual a soma dos quadrados dos resíduos ou erros é?

a) Estacionária  
b) Uniforme  
c) Mínima  
d) Máxima  

### Questão 34

O que é que a auto covariância mede numa série temporal?

a) Dependência linear entre múltiplos pontos de diferentes séries temporais em diferentes momentos  
b) Dependência quadrática entre dois pontos da mesma série temporal em momentos diferentes  
c) Dependência linear entre dois pontos de séries temporais diferentes observadas no mesmo momento  
d) Dependência linear entre dois pontos da mesma série temporal em momentos diferentes  

**Questão 35**

A figura apresenta um gráfico da função de autocorrelação parcial (PACF). Com base neste gráfico indique qual o modelo autorregressivo apropriado. (devem clicar na imagem para a ver com maiores dimensões)

![](https://s3.us-east-2.amazonaws.com/cbs.pg.repository/teste_35.png)

a) AR(1)  
b) AR(2)  
c) AR(3)  
d) AR(4)

**Questão 36**

__________ analisa a relação entre as variáveis independentes e a dependente.

a) K-means clustering  
b) Big data  
c) Aprendizagem não supervisionada  
d) Análise de regressão

**Questão 37**

Imagine que trabalha para um serviço de streaming de música e quer utilizar a aprendizagem supervisionada para classificar a música em diferentes géneros. O seu serviço já recolheu milhares de canções em cada género, e utilizou-as como dados de treino. Agora retira um pequeno subconjunto aleatório de todas as canções do seu serviço. Como se chama este subconjunto?

a) Conjunto de teste  
b) Cluster de dados  
c) Overfitting  
d) Big Data

**Questão 38**

Imagine que trabalha para uma gelataria e criou o gráfico igual ao da figura, que mostra a relação entre a temperatura exterior e a venda de gelados. Qual é a melhor descrição deste gráfico?

![](https://s3.us-east-2.amazonaws.com/cbs.pg.repository/teste_38.png)

a) É um gráfico de aprendizagem não supervisionada  
b) É um gráfico de uma árvore de decisão  
c) É um gráfico de uma regressão linear  
d) É um gráfico de clustering

**Questão 39**

Qual dos seguintes gráficos, se algum, apresenta um modelo a sofrer de overfitting? (devem clicar na imagem para a ver com maiores dimensões)

![](https://s3.us-east-2.amazonaws.com/cbs.pg.repository/teste_39.png)

a) O gráfico mais à esquerda da figura  
b) O gráfico no meio da figura  
c) O gráfico mais à direita da figura  
d) Nenhum dos gráficos da figura  

**Questão 40**

O resultado do processo de treino em machine learning é ____________

a) um algoritmo de machine learning  
b) um modelo de machine learning  
c) a exatidão do algoritmo de machine learning  
d) a precisão do algoritmo de machine learning  